In [ ]:
# from datasets import load_dataset

# print("Loading the text data from bentrevett/multi30k...")
# text_dataset = load_dataset("bentrevett/multi30k")
# print("Text data loaded successfully.")
# print(text_dataset)

Loading the text data from bentrevett/multi30k...
Text data loaded successfully.
DatasetDict({
    train: Dataset({
        features: ['en', 'de'],
        num_rows: 29000
    })
    validation: Dataset({
        features: ['en', 'de'],
        num_rows: 1014
    })
    test: Dataset({
        features: ['en', 'de'],
        num_rows: 1000
    })
})


In [ ]:
# # These commands download the Flickr30k image dataset
# !wget "https://github.com/awsaf49/flickr-dataset/releases/download/v1.0/flickr30k_part00"
# !wget "https://github.com/awsaf49/flickr-dataset/releases/download/v1.0/flickr30k_part01"
# !wget "https://github.com/awsaf49/flickr-dataset/releases/download/v1.0/flickr30k_part02"

# print("Downloaded and extracted Flickr30k images successfully into the 'flickr30k' folder.")

--2025-10-03 01:54:15--  https://github.com/awsaf49/flickr-dataset/releases/download/v1.0/flickr30k_part00
Resolving github.com (github.com)... 20.207.73.82
Connecting to github.com (github.com)|20.207.73.82|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://release-assets.githubusercontent.com/github-production-release-asset/753516996/b878d7ef-9eca-4c26-90d5-463215017d7a?sp=r&sv=2018-11-09&sr=b&spr=https&se=2025-10-02T21%3A24%3A05Z&rscd=attachment%3B+filename%3Dflickr30k_part00&rsct=application%2Foctet-stream&skoid=96c2d410-5711-43a1-aedd-ab1947aa7ab0&sktid=398a6654-997b-47e9-b12b-9515b896b4de&skt=2025-10-02T20%3A23%3A51Z&ske=2025-10-02T21%3A24%3A05Z&sks=b&skv=2018-11-09&sig=dUKHUnmItpA4jWM6lR1v9Miob5qLLXYDy66PEsD8p6w%3D&jwt=eyJ0eXAiOiJKV1QiLCJhbGciOiJIUzI1NiJ9.eyJpc3MiOiJnaXRodWIuY29tIiwiYXVkIjoicmVsZWFzZS1hc3NldHMuZ2l0aHVidXNlcmNvbnRlbnQuY29tIiwia2V5Ijoia2V5MSIsImV4cCI6MTc1OTQ0MDI0OSwibmJmIjoxNzU5NDM2NjQ5LCJwYXRoIjoicmVsZWFzZWFzc2V0cHJvZHVjdGlvbi5

Downloaded and extracted Flickr30k images successfully into the 'flickr30k' folder.


'rm' is not recognized as an internal or external command,
operable program or batch file.


In [ ]:
# import os
# import zipfile

# print("Combining downloaded parts...")
# # List the downloaded parts in order
# parts = ['flickr30k_part00', 'flickr30k_part01', 'flickr30k_part02']
# zip_filename = 'flickr30k.zip'

# # Open the final zip file in write-binary mode
# with open(zip_filename, 'wb') as f_out:
#     for part_name in parts:
#         # Open each part in read-binary mode
#         with open(part_name, 'rb') as f_in:
#             # Read the content from the part and write it to the final zip file
#             f_out.write(f_in.read())

# print(f"'{zip_filename}' created successfully.")

# # Unzip the file
# print(f"Extracting '{zip_filename}'...")
# output_dir = './flickr30k'
# with zipfile.ZipFile(zip_filename, 'r') as zip_ref:
#     zip_ref.extractall(output_dir)
# print(f"Images extracted to '{output_dir}' folder.")

# # Clean up the temporary files
# print("Cleaning up temporary files...")
# os.remove(zip_filename)
# for part_name in parts:
#     os.remove(part_name)
# print("Cleanup complete.")

Combining downloaded parts...
'flickr30k.zip' created successfully.
Extracting 'flickr30k.zip'...
Images extracted to './flickr30k' folder.
Cleaning up temporary files...
Cleanup complete.


In [1]:
import os
import gzip
from datasets import Dataset, DatasetDict, Image as HFImage

# --- Configuration ---
# Path to your existing image folder.
image_folder_path = os.path.join("flickr30k", "Images") 

# Path to the 'dataset' repository you cloned.
repo_path = "dataset"

# --- Verification ---
if not os.path.isdir(image_folder_path):
    print(f"❌ ERROR: Your image folder was not found at '{image_folder_path}'")
elif not os.path.isdir(repo_path):
    print(f"❌ ERROR: The repository folder '{repo_path}' was not found.")
else:
    print("✅ Image and repository folders found. Assembling the dataset...")

    # --- Assemble the Dataset from Local Files ---
    dataset_dict = {}
    
    # CORRECTED: Added .gz to all text filenames
    split_map = {
        "train": {"en": "train.en.gz", "de": "train.de.gz", "files": "train.txt"},
        "validation": {"en": "val.en.gz", "de": "val.de.gz", "files": "val.txt"},
        "test": {"en": "test_2016_flickr.en.gz", "de": "test_2016_flickr.de.gz", "files": "test_2016_flickr.txt"}
    }

    text_path = os.path.join(repo_path, "data", "task1", "raw")
    files_path = os.path.join(repo_path, "data", "task1", "image_splits")

    for split_name, paths in split_map.items():
        print(f"Processing split: {split_name}")
        
        en_file_path = os.path.join(text_path, paths['en'])
        de_file_path = os.path.join(text_path, paths['de'])
        img_list_path = os.path.join(files_path, paths['files'])
        
        # CORRECTED: Use gzip.open() to read the compressed files in text mode ('rt')
        with gzip.open(en_file_path, 'rt', encoding='utf-8') as f: en_sents = f.read().strip().split('\n')
        with gzip.open(de_file_path, 'rt', encoding='utf-8') as f: de_sents = f.read().strip().split('\n')
        
        # The image list file is not compressed, so we read it normally
        with open(img_list_path, 'r', encoding='utf-8') as f: img_files = f.read().strip().split('\n')

        data = {
            'image': [os.path.join(image_folder_path, fname) for fname in img_files],
            'en': en_sents,
            'de': de_sents
        }
        
        hf_dataset = Dataset.from_dict(data).cast_column("image", HFImage())
        dataset_dict[split_name] = hf_dataset

    final_dataset = DatasetDict(dataset_dict)

    print("\n✅ Dataset created successfully!")
    print(final_dataset)

    # --- Final Verification ---
    print("\n--- Verifying First Training Example ---")
    example = final_dataset['train'][0]
    print(f"English: {example['en']}")
    print(f"German: {example['de']}")
    print(f"Image: {example['image']}")
    print("--------------------------------------")

✅ Image and repository folders found. Assembling the dataset...
Processing split: train
Processing split: validation
Processing split: test

✅ Dataset created successfully!
DatasetDict({
    train: Dataset({
        features: ['image', 'en', 'de'],
        num_rows: 29000
    })
    validation: Dataset({
        features: ['image', 'en', 'de'],
        num_rows: 1014
    })
    test: Dataset({
        features: ['image', 'en', 'de'],
        num_rows: 1000
    })
})

--- Verifying First Training Example ---
English: Two young, White males are outside near many bushes.
German: Zwei junge weiße Männer sind im Freien in der Nähe vieler Büsche.
Image: <PIL.JpegImagePlugin.JpegImageFile image mode=RGB size=333x500 at 0x239F8177010>
--------------------------------------


In [2]:
import torch
from transformers import CLIPProcessor, CLIPModel
from tqdm import tqdm
import os

# --- 1. Load Pre-trained CLIP Model ---
print("Loading CLIP model and processor...")
# Using a standard CLIP model from OpenAI
model_name = "openai/clip-vit-base-patch32" 
device = "cuda" if torch.cuda.is_available() else "cpu"

model = CLIPModel.from_pretrained(model_name).to(device)
processor = CLIPProcessor.from_pretrained(model_name)
print(f"Model loaded and moved to {device}.")

# --- 2. Function to Extract and Save Features ---
def extract_and_save_features(dataset_split, split_name, output_dir="clip_features"):
    """Processes a dataset split and saves image features to disk."""
    
    split_dir = os.path.join(output_dir, split_name)
    os.makedirs(split_dir, exist_ok=True)
    print(f"\nProcessing '{split_name}' split... Saving features to '{split_dir}'")
    
    # Loop through the dataset with a progress bar
    for i, example in enumerate(tqdm(dataset_split)):
        image = example['image']
        
        # Path where we will save the feature tensor
        feature_path = os.path.join(split_dir, f"{i}.pt")
        
        # To save time, skip if this feature has already been extracted
        if os.path.exists(feature_path):
            continue
        
        # We don't need to calculate gradients for this, so torch.no_grad() is used for efficiency
        with torch.no_grad():
            # Process the image and prepare it for the model
            inputs = processor(images=image, return_tensors="pt").to(device)
            
            # Get the image features (the embedding)
            image_features = model.get_image_features(**inputs)
            
            # Save the feature tensor to a file.
            # It's good practice to move tensors to the CPU before saving.
            torch.save(image_features.cpu(), feature_path)

# --- 3. Run Extraction for All Splits ---
# `final_dataset` is the DatasetDict you successfully created in the previous step
extract_and_save_features(final_dataset['train'], 'train')
extract_and_save_features(final_dataset['validation'], 'validation')
extract_and_save_features(final_dataset['test'], 'test')

print("\n\n✅ Stage 2 Complete: All visual features have been extracted and saved!")

Loading CLIP model and processor...
Model loaded and moved to cuda.

Processing 'train' split... Saving features to 'clip_features\train'


100%|██████████| 29000/29000 [05:52<00:00, 82.16it/s] 



Processing 'validation' split... Saving features to 'clip_features\validation'


100%|██████████| 1014/1014 [00:09<00:00, 108.50it/s]



Processing 'test' split... Saving features to 'clip_features\test'


100%|██████████| 1000/1000 [00:09<00:00, 101.10it/s]



✅ Stage 2 Complete: All visual features have been extracted and saved!


STAGE 3

In [3]:
import torch
import torch.nn as nn
from torch.utils.data import Dataset, DataLoader
import os
from tokenizers import Tokenizer

# --- 1. Setup ---
# Make sure you have your tokenizers loaded and special indices defined,
# just like in your original training script (1A.ipynb).

print("Loading tokenizers...")
tokenizer_en = Tokenizer.from_file("tokenizer_en.json")
tokenizer_de = Tokenizer.from_file("tokenizer_de.json")
UNK_IDX, PAD_IDX, SOS_IDX, EOS_IDX = 0, 1, 2, 3
print("Tokenizers loaded.")

# --- 2. Create a Custom PyTorch Dataset Class ---
# This class wraps our dataset and loads the correct text and image feature for a given index.

class MultiModalDataset(Dataset):
    def __init__(self, hf_dataset_split, feature_dir):
        """
        hf_dataset_split: One of the splits from the DatasetDict (e.g., final_dataset['train'])
        feature_dir: The directory containing the saved .pt feature files for that split.
        """
        self.hf_dataset = hf_dataset_split
        self.feature_dir = feature_dir

    def __len__(self):
        return len(self.hf_dataset)

    def __getitem__(self, idx):
        # Get the English and German sentences from the Hugging Face dataset
        text_data = self.hf_dataset[idx]
        src_sentence = text_data['en']
        tgt_sentence = text_data['de']

        # Construct the path to the corresponding CLIP feature file and load it
        feature_path = os.path.join(self.feature_dir, f"{idx}.pt")
        image_feature = torch.load(feature_path)
        
        # The saved feature has a shape of [1, 512]. We squeeze it to [512] for easier batching.
        image_feature = image_feature.squeeze(0)

        return src_sentence, tgt_sentence, image_feature

# --- 3. Create the Collate Function ---
# This function takes a list of samples from our Dataset and bundles them into padded tensors.

def create_multimodal_batch(data_batch):
    src_batch, tgt_batch, img_batch = [], [], []
    
    for src_item, tgt_item, img_item in data_batch:
        # Tokenize the text sentences and add Start-of-Sentence/End-of-Sentence tokens
        src_tokens = [SOS_IDX] + tokenizer_en.encode(src_item).ids + [EOS_IDX]
        tgt_tokens = [SOS_IDX] + tokenizer_de.encode(tgt_item).ids + [EOS_IDX]
        
        src_batch.append(torch.tensor(src_tokens, dtype=torch.long))
        tgt_batch.append(torch.tensor(tgt_tokens, dtype=torch.long))
        img_batch.append(img_item)
        
    # Pad the text sequences to the same length within the batch
    src_padded = nn.utils.rnn.pad_sequence(src_batch, padding_value=PAD_IDX)
    tgt_padded = nn.utils.rnn.pad_sequence(tgt_batch, padding_value=PAD_IDX)
    
    # Stack the individual image features into a single tensor for the batch
    img_features = torch.stack(img_batch)
    
    return src_padded, tgt_padded, img_features

# --- 4. Instantiate and Test the New DataLoaders ---
BATCH_SIZE = 32 # Use the same batch size as your previous training

# Create instances of our custom dataset for the train and validation splits
train_dataset = MultiModalDataset(final_dataset['train'], "clip_features/train")
val_dataset = MultiModalDataset(final_dataset['validation'], "clip_features/validation")

# Create the DataLoaders that will use our custom dataset and collate function
train_dataloader = DataLoader(train_dataset, batch_size=BATCH_SIZE, collate_fn=create_multimodal_batch, shuffle=True)
val_dataloader = DataLoader(val_dataset, batch_size=BATCH_SIZE, collate_fn=create_multimodal_batch)

print("\n--- Testing the new train_dataloader ---")
# Get one batch of data to verify everything is working
src_batch, tgt_batch, img_batch = next(iter(train_dataloader))

print("\n--- Batch Shapes ---")
print(f"Source Text Batch Shape:    {src_batch.shape}")
print(f"Target Text Batch Shape:    {tgt_batch.shape}")
print(f"Image Features Batch Shape: {img_batch.shape}")
print("--------------------")

print("\nExplanation of Shapes:")
print(" - Text shapes are (SequenceLength, BatchSize). 'SequenceLength' will vary for each batch.")
print(" - Image features shape is (BatchSize, FeatureDimension). The feature dimension should be 512, as expected from CLIP.")

Loading tokenizers...
Tokenizers loaded.

--- Testing the new train_dataloader ---

--- Batch Shapes ---
Source Text Batch Shape:    torch.Size([29, 32])
Target Text Batch Shape:    torch.Size([28, 32])
Image Features Batch Shape: torch.Size([32, 512])
--------------------

Explanation of Shapes:
 - Text shapes are (SequenceLength, BatchSize). 'SequenceLength' will vary for each batch.
 - Image features shape is (BatchSize, FeatureDimension). The feature dimension should be 512, as expected from CLIP.


In [4]:
import torch
import torch.nn as nn
import math

# These helper classes are the same as in your original model
class PositionalEncoding(nn.Module):
    def __init__(self, emb_size: int, dropout: float, maxlen: int = 5000):
        super(PositionalEncoding, self).__init__()
        den = torch.exp(-torch.arange(0, emb_size, 2) * math.log(10000) / emb_size)
        pos = torch.arange(0, maxlen).reshape(maxlen, 1)
        pos_embedding = torch.zeros((maxlen, emb_size))
        pos_embedding[:, 0::2] = torch.sin(pos * den)
        pos_embedding[:, 1::2] = torch.cos(pos * den)
        pos_embedding = pos_embedding.unsqueeze(-2)
        self.dropout = nn.Dropout(dropout)
        self.register_buffer('pos_embedding', pos_embedding)

    def forward(self, token_embedding):
        return self.dropout(token_embedding + self.pos_embedding[:token_embedding.size(0), :])

class TokenEmbedding(nn.Module):
    def __init__(self, vocab_size: int, emb_size):
        super(TokenEmbedding, self).__init__()
        self.embedding = nn.Embedding(vocab_size, emb_size)
        self.emb_size = emb_size

    def forward(self, tokens):
        return self.embedding(tokens.long()) * math.sqrt(self.emb_size)

# --- The NEW Multi-Modal Transformer Model ---
# --- The CORRECTED Multi-Modal Transformer Model ---
class MultiModalTransformer(nn.Module):
    def __init__(self,
                 num_encoder_layers: int,
                 num_decoder_layers: int,
                 emb_size: int,
                 nhead: int,
                 src_vocab_size: int,
                 tgt_vocab_size: int,
                 dim_feedforward: int,
                 dropout: float = 0.1,
                 clip_feature_dim: int = 512):
        super().__init__()
        
        self.transformer = nn.Transformer(d_model=emb_size, nhead=nhead, num_encoder_layers=num_encoder_layers,
                                          num_decoder_layers=num_decoder_layers, dim_feedforward=dim_feedforward,
                                          dropout=dropout)
        
        self.generator = nn.Linear(emb_size, tgt_vocab_size)
        self.src_tok_emb = TokenEmbedding(src_vocab_size, emb_size)
        self.tgt_tok_emb = TokenEmbedding(tgt_vocab_size, emb_size)
        self.positional_encoding = PositionalEncoding(emb_size, dropout=dropout)
        self.clip_projection = nn.Linear(clip_feature_dim, emb_size)

    # === CORRECTED: Simplified the forward method's arguments ===
    def forward(self,
                src,
                trg,
                image_features,
                src_mask,
                tgt_mask,
                src_padding_mask,
                tgt_padding_mask): # Removed the last argument
        
        src_text_emb = self.positional_encoding(self.src_tok_emb(src))
        projected_img_emb = self.clip_projection(image_features).unsqueeze(0)
        encoder_input = torch.cat([projected_img_emb, src_text_emb], dim=0)
        tgt_emb = self.positional_encoding(self.tgt_tok_emb(trg))

        batch_size = src.shape[1]
        image_mask = torch.zeros((batch_size, 1), dtype=torch.bool, device=src.device)
        adjusted_src_padding_mask = torch.cat([image_mask, src_padding_mask], dim=1)

        # === CORRECTED: Use the adjusted mask for the memory_key_padding_mask as well ===
        outs = self.transformer(encoder_input, tgt_emb, src_mask, tgt_mask, None,
                                adjusted_src_padding_mask, # For the encoder
                                tgt_padding_mask,          # For the decoder
                                adjusted_src_padding_mask) # For the decoder's attention to the encoder
        
        return self.generator(outs)

In [5]:
import torch
import torch.nn as nn
from tqdm import tqdm
import math

# --- 1. Hyperparameters and Setup ---
# These are the same as your original model.
DEVICE = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
print(f"Using device: {DEVICE}")

SRC_VOCAB_SIZE = 10000
TGT_VOCAB_SIZE = 10000
EMB_SIZE = 256
NHEAD = 8
FFN_HID_DIM = 512
NUM_ENCODER_LAYERS = 3
NUM_DECODER_LAYERS = 3
BATCH_SIZE = 32
NUM_EPOCHS = 50 # You can increase this later for better performance
LEARNING_RATE = 0.0001

# --- 2. Model, Loss, and Optimizer ---
# Instantiate the NEW MultiModalTransformer
model = MultiModalTransformer(NUM_ENCODER_LAYERS, NUM_DECODER_LAYERS, EMB_SIZE,
                              NHEAD, SRC_VOCAB_SIZE, TGT_VOCAB_SIZE, FFN_HID_DIM)
model = model.to(DEVICE)

# Initialize weights
for p in model.parameters():
    if p.dim() > 1:
        nn.init.xavier_uniform_(p)

loss_fn = torch.nn.CrossEntropyLoss(ignore_index=PAD_IDX)
optimizer = torch.optim.Adam(model.parameters(), lr=LEARNING_RATE, betas=(0.9, 0.98), eps=1e-9)

# Helper for generating masks
def generate_square_subsequent_mask(sz, device):
    mask = (torch.triu(torch.ones((sz, sz), device=device)) == 1).transpose(0, 1)
    mask = mask.float().masked_fill(mask == 0, float('-inf')).masked_fill(mask == 1, float(0.0))
    return mask

# --- 3. MODIFIED Training and Evaluation Functions ---
# --- The CORRECTED Training and Evaluation Functions ---
def train_epoch(model, optimizer, dataloader):
    model.train()
    losses = 0
    
    for src, tgt, image_features in tqdm(dataloader, desc="Training"):
        src, tgt, image_features = src.to(DEVICE), tgt.to(DEVICE), image_features.to(DEVICE)

        tgt_input = tgt[:-1, :]
        tgt_out = tgt[1:, :]

        src_seq_len, tgt_seq_len = src.shape[0], tgt_input.shape[0]
        
        tgt_mask = generate_square_subsequent_mask(tgt_seq_len, DEVICE)
        src_mask = torch.zeros((src_seq_len + 1, src_seq_len + 1), device=DEVICE).type(torch.bool)
        
        src_padding_mask = (src == PAD_IDX).transpose(0, 1)
        tgt_padding_mask = (tgt_input == PAD_IDX).transpose(0, 1)

        # === CORRECTED: Simplified the model call ===
        logits = model(src, tgt_input, image_features, src_mask, tgt_mask, src_padding_mask, tgt_padding_mask)

        optimizer.zero_grad()
        loss = loss_fn(logits.reshape(-1, logits.shape[-1]), tgt_out.reshape(-1))
        loss.backward()
        optimizer.step()
        losses += loss.item()

    return losses / len(list(dataloader))

def evaluate(model, dataloader):
    model.eval()
    losses = 0

    with torch.no_grad():
        for src, tgt, image_features in tqdm(dataloader, desc="Validating"):
            src, tgt, image_features = src.to(DEVICE), tgt.to(DEVICE), image_features.to(DEVICE)

            tgt_input = tgt[:-1, :]
            tgt_out = tgt[1:, :]

            src_seq_len, tgt_seq_len = src.shape[0], tgt_input.shape[0]
            tgt_mask = generate_square_subsequent_mask(tgt_seq_len, DEVICE)
            src_mask = torch.zeros((src_seq_len + 1, src_seq_len + 1), device=DEVICE).type(torch.bool)
            src_padding_mask = (src == PAD_IDX).transpose(0, 1)
            tgt_padding_mask = (tgt_input == PAD_IDX).transpose(0, 1)

            # === CORRECTED: Simplified the model call ===
            logits = model(src, tgt_input, image_features, src_mask, tgt_mask, src_padding_mask, tgt_padding_mask)
            
            loss = loss_fn(logits.reshape(-1, logits.shape[-1]), tgt_out.reshape(-1))
            losses += loss.item()

    return losses / len(list(dataloader))

# --- 4. Main Training Loop ---
best_val_loss = float('inf')

for epoch in range(1, NUM_EPOCHS + 1):
    train_loss = train_epoch(model, optimizer, train_dataloader)
    val_loss = evaluate(model, val_dataloader)

    print(f"Epoch: {epoch}, Train loss: {train_loss:.3f}, Val loss: {val_loss:.3f}")
    
    if val_loss < best_val_loss:
        best_val_loss = val_loss
        torch.save(model.state_dict(), 'best_multimodal_model.pth')
        print(f"Saved new best model to 'best_multimodal_model.pth'")

print("\n\n✅ Training complete. Best multi-modal model saved.")

Using device: cuda


c:\Users\Hp\AppData\Local\Programs\Python\Python310\lib\site-packages\torch\nn\modules\transformer.py:392: UserWarning: enable_nested_tensor is True, but self.use_nested_tensor is False because encoder_layer.self_attn.batch_first was not True(use batch_first for better inference performance)
  warnings.warn(
Training:   0%|          | 0/907 [00:00<?, ?it/s]c:\Users\Hp\AppData\Local\Programs\Python\Python310\lib\site-packages\torch\nn\functional.py:6041: UserWarning: Support for mismatched key_padding_mask and attn_mask is deprecated. Use same type for both instead.
  warnings.warn(
Validating: 100%|██████████| 32/32 [00:22<00:00,  1.43it/s]


Epoch: 1, Train loss: 5.326, Val loss: 4.379
Saved new best model to 'best_multimodal_model.pth'


Validating: 100%|██████████| 32/32 [00:05<00:00,  5.68it/s]


Epoch: 2, Train loss: 4.002, Val loss: 3.683
Saved new best model to 'best_multimodal_model.pth'


...

Epoch: 48, Train loss: 0.592, Val loss: 2.284


Validating: 100%|██████████| 32/32 [00:03<00:00,  9.10it/s]


Epoch: 49, Train loss: 0.574, Val loss: 2.281


Validating: 100%|██████████| 32/32 [00:03<00:00,  8.39it/s]


Epoch: 50, Train loss: 0.560, Val loss: 2.271


✅ Training complete. Best multi-modal model saved.
